In [ ]:
import scipy as sci
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import animation
from mpl_toolkits.mplot3d import Axes3D
import numpy as np
import scipy.integrate

In [ ]:
#quantities
G=6.67408e-11
mass=1.989e+30 
distance=5.326e+12
speed=30000
time=50*365*24*3600

#scale factors
C1=(G*time*mass)/(distance**2*speed)
C2=(speed*time)/(distance)

In [ ]:
#masses
M1=1.102
M2=0.902
M3=1.502


#initial positions:
ro1=np.array([-0.5,1,0])
ro2=np.array([0.5,0,0.5])
ro3=np.array([1.5,1,1.5])

#initial velocities
vo1=np.array([0.02,0.02,0.02])
vo2=np.array([-0.05,0,-0.1]) 
vo3=np.array([0,-0.03,0])

#center of mass
r_com=(M1*ro1+M2*ro2+M3*ro3)/(M1+M2+M3)
v_com=(M1*vo1+M2*vo2+M3*vo3)/(M1+M2+M3)

In [ ]:
y = np.concatenate((ro1, ro2, ro3, vo1, vo2, vo3))
print(y)
print(y.shape)

In [ ]:
def KeplerODE(y,t):
    global M1,M2,M3,G
    
    #positions
    r1=y[:3]
    r2=y[3:6]
    r3=y[6:9]
    
    #velocities
    v1=y[9:12]
    v2=y[12:15]
    v3=y[15:18]
    
    #Distances between the objects
    r12=sci.linalg.norm(r2-r1)
    r13=sci.linalg.norm(r3-r1)
    r23=sci.linalg.norm(r3-r2)

    
    #Derivatives
    dr1dt = C2*v1
    dr2dt = C2*v2
    dr3dt = C2*v3
    
    dv1dt = C1*M2*(r2-r1)/r12**3+C1*M3*(r3-r1)/r13**3
    dv2dt = C1*M1*(r1-r2)/r12**3+C1*M3*(r3-r2)/r23**3
    dv3dt = C1*M1*(r1-r3)/r13**3+C1*M2*(r2-r3)/r23**3
    
    #Combine derivatives
    derivatives = np.concatenate((dr1dt,dr2dt,dr3dt,dv1dt,dv2dt,dv3dt))
    return derivatives

In [ ]:
initial_parameters = y
t=np.linspace(0,20,1000)
print(initial_parameters)

In [ ]:
three_body_sol=sci.integrate.odeint(KeplerODE,initial_parameters,t)

r1_sol=three_body_sol[:,:3]
r2_sol=three_body_sol[:,3:6]
r3_sol=three_body_sol[:,6:9]

In [ ]:
#static plot of outcome

fig=plt.figure(figsize=(15,15))

ax=fig.add_subplot(111,projection="3d")

ax.set_facecolor('black')

#trails
ax.plot(r1_sol[:,0],r1_sol[:,1],r1_sol[:,2],color="purple")
ax.plot(r2_sol[:,0],r2_sol[:,1],r2_sol[:,2],color="magenta")
ax.plot(r3_sol[:,0],r3_sol[:,1],r3_sol[:,2],color="gold")

#ax.grid(False)

ax.set_facecolor('black')
ax.xaxis.label.set_color('gold')        
ax.yaxis.label.set_color('gold')
ax.zaxis.label.set_color('gold')  

ax.tick_params(axis='x', colors='gold')   
ax.tick_params(axis='y', colors='gold') 
ax.tick_params(axis='z', colors='gold')  

ax.spines['left'].set_color('gold')        
ax.spines['top'].set_color('gold')

#stars
ax.scatter(r1_sol[-1,0],r1_sol[-1,1],r1_sol[-1,2],color="purple",marker="o",s=80,label="Star 1")
ax.scatter(r2_sol[-1,0],r2_sol[-1,1],r2_sol[-1,2],color="magenta",marker="o",s=80,label="Star 2")
ax.scatter(r3_sol[-1,0],r3_sol[-1,1],r3_sol[-1,2],color="gold",marker="o",s=80,label="Star 3")

ax.set_xlabel("x-axis",fontsize=14)
ax.set_ylabel("y-axis",fontsize=14)
ax.set_zlabel("z-axis",fontsize=14)



ax.set_title("Three Body System\n",fontsize=21)
ax.axes.set_xlim3d(left=-2, right=4) 
ax.axes.set_ylim3d(bottom=-2, top=3) 
ax.axes.set_zlim3d(bottom=-4, top=2)
ax.legend(loc="upper right",fontsize=14)

In [ ]:
#animation of plot

fig=plt.figure(figsize=(15,15))
ax=fig.add_subplot(111,projection="3d")

#ax.grid(False)

ax.set_facecolor('black')
ax.xaxis.label.set_color('gold')        
ax.yaxis.label.set_color('gold')
ax.zaxis.label.set_color('gold')  

ax.tick_params(axis='x', colors='gold')   
ax.tick_params(axis='y', colors='gold') 
ax.tick_params(axis='z', colors='gold')  

ax.spines['left'].set_color('gold')        
ax.spines['top'].set_color('gold')

star1_anim=r1_sol[::1,:].copy()
star2_anim=r2_sol[::1,:].copy()
star3_anim=r3_sol[::1,:].copy()


star1=[ax.scatter(star1_anim[0,0],star1_anim[0,1],star1_anim[0,2],color="purple",marker="o",s=80,label="Star 1 (1.102 Solar Masses)")]
star2=[ax.scatter(star2_anim[0,0],star2_anim[0,1],star2_anim[0,2],color="magenta",marker="o",s=80,label="Star 2 (0.902 Solar Masses)")]
star3=[ax.scatter(star3_anim[0,0],star3_anim[0,1],star3_anim[0,2],color="gold",marker="o",s=80,label="Star 3 (1.502 Solar Masses)")]

def Animation(frame_number,star1,star2,star3):
    #remove markers
    star1[0].remove()
    star2[0].remove()
    star3[0].remove()
    
    #orbits
    trail1=ax.plot(star1_anim[:frame_number,0],star1_anim[:frame_number,1],star1_anim[:frame_number,2],color="purple")
    trail2=ax.plot(star2_anim[:frame_number,0],star2_anim[:frame_number,1],star2_anim[:frame_number,2],color="magenta")
    trail3=ax.plot(star3_anim[:frame_number,0],star3_anim[:frame_number,1],star3_anim[:frame_number,2],color="gold")
    
    #plot new markers
    star1[0]=ax.scatter(star1_anim[frame_number-1,0],star1_anim[frame_number-1,1],star1_anim[frame_number-1,2],color="purple",marker="o",s=100)
    star2[0]=ax.scatter(star2_anim[frame_number-1,0],star2_anim[frame_number-1,1],star2_anim[frame_number-1,2],color="magenta",marker="o",s=100)
    star3[0]=ax.scatter(star3_anim[frame_number-1,0],star3_anim[frame_number-1,1],star3_anim[frame_number-1,2],color="gold",marker="o",s=100)
    return trail1,trail2,trail3,star1,star2,star3


ax.set_xlabel("x-axis",fontsize=15)
ax.set_ylabel("y-axis",fontsize=15)
ax.set_zlabel("z-axis",fontsize=15)
ax.set_title("Three Body System with Solar Masses 1.102, 0.902, and 1.502\n",fontsize=21)

ax.axes.set_xlim3d(left=-2, right=4) 
ax.axes.set_ylim3d(bottom=-2, top=3) 
ax.axes.set_zlim3d(bottom=-4, top=2)

ax.legend(loc="upper right",fontsize=14)

anim=animation.FuncAnimation(fig,Animation,frames=800,interval=10,repeat=False,blit=False,fargs=(star1,star2,star3))

# Set up formatting for the movie files
#Writer = animation.writers['ffmpeg']
writer = animation.writers['ffmpeg'](fps=30, metadata=dict(artist='Firethunder'), bitrate=4000)

#To save animation to disk, enable this command
anim.save("animation3.mp4", writer=writer)